In [1]:
!pip install torchsummary
!pip install scikit-learn
!pip install split-folders
!pip install pandas
!pip install opencv-python
!pip install albumentations

In [2]:
import os
import pandas as pd
import numpy as np
import torch
import torch.nn as nn
import torch.optim as optim
from torch.autograd import Variable
import torchvision.datasets as dset
import torchvision.transforms as transforms
import albumentations as A
from albumentations.pytorch.transforms import ToTensorV2
import torch.nn.functional as F
from torch.utils.data import Dataset
from torch.utils.data import DataLoader
import torchvision.models as models
import cv2
import sys
import math
import random
import splitfolders
import torchsummary
from tqdm.auto import tqdm
from resnet import ResNet18
from sklearn.model_selection import train_test_split
from sklearn.model_selection import cross_val_score
from sklearn.metrics import f1_score

In [3]:
torch.cuda.is_available()

True

In [4]:
data_path = './userdata/user04'

user_dir_list = os.listdir(data_path)

user_label_list = []
for element in user_dir_list:
    label_data_path = data_path + '/' + element + '/' + element + '_label.csv'
    label_data = pd.read_csv(label_data_path)
    user_label_list.append(label_data)

df = pd.concat(user_label_list)
tmp_df = df
# df['ts'] = pd.to_datetime(df['ts'], unit='s')
df = df.sort_values('ts')
df = df.drop(columns=['actionSub', 'actionSubOption', 'condition', 'conditionSub1Option', 'conditionSub2Option', 'place', 'emotionPositive', 'emotionTension'])

df.head()

ts         action  actionOption  activity
0  1.598828e+09  personal_care           132         3
1  1.598828e+09  personal_care           132         3
2  1.598829e+09  personal_care           132         3
3  1.598829e+09  personal_care           132         3
4  1.598829e+09  personal_care           132         3

In [5]:
len(df)

22120

In [6]:
df['actionOption'].value_counts()

211    8517
121    1842
82     1810
712    1371
87     1031
41      947
756     922
212     859
724     748
793     662
711     601
725     444
132     420
751     344
133     283
213     256
752     250
43      205
122     163
81      134
46      120
84       49
762      48
92       40
42       40
722      14
Name: actionOption, dtype: int64

In [7]:
len(df['actionOption'].value_counts())

26

In [8]:
rp_data_path = './RPdata/user04/'
tmp_path = rp_data_path + '/1598828400/RP/'
tmp_list_dir = os.listdir(tmp_path)

In [9]:
tmp_list_dir.sort()
tmp_list_dir

['1598829240.png',
 '1598829300.png',
 '1598829360.png',
 '1598829420.png',
 '1598829480.png',
 '1598829540.png',
 '1598829600.png',
 '1598829660.png',
 '1598830200.png',
 '1598830260.png',
 '1598830320.png',
 '1598830380.png',
 '1598830440.png',
 '1598830500.png',
 '1598830560.png',
 '1598830620.png',
 '1598830680.png',
 '1598830740.png',
 '1598830800.png',
 '1598830860.png',
 '1598830920.png',
 '1598830980.png',
 '1598831040.png',
 '1598831100.png',
 '1598831160.png',
 '1598831220.png',
 '1598831280.png',
 '1598831340.png',
 '1598832000.png',
 '1598832060.png',
 '1598832120.png',
 '1598832180.png',
 '1598832240.png',
 '1598832300.png',
 '1598832360.png',
 '1598832420.png',
 '1598832480.png',
 '1598832540.png',
 '1598832600.png',
 '1598832660.png',
 '1598832720.png',
 '1598832780.png',
 '1598832840.png',
 '1598832900.png',
 '1598832960.png',
 '1598833020.png',
 '1598833080.png',
 '1598833140.png',
 '1598833200.png',
 '1598833260.png',
 '1598833320.png',
 '1598833380.png',
 '1598833440

In [10]:
tmp_list_dir[0][:-4]

'1598829240'

In [11]:
df[df['ts'] == 1598829240]

ts action  actionOption  activity
14  1.598829e+09   meal           121         4

In [12]:
df['ts'] = df['ts'].apply(lambda x : str(x)[:-2])

In [13]:
df

ts         action  actionOption  activity
0    1598828400  personal_care           132         3
1    1598828460  personal_care           132         3
2    1598828520  personal_care           132         3
3    1598828580  personal_care           132         3
4    1598828640  personal_care           132         3
..          ...            ...           ...       ...
764  1601208840    outdoor_act           751         4
765  1601208900    outdoor_act           751         3
766  1601208960    outdoor_act           751         3
767  1601209020    outdoor_act           751         3
768  1601209080    outdoor_act           751         3

[22120 rows x 4 columns]

In [14]:
rp_dir_list = os.listdir(rp_data_path)
rp_df = pd.DataFrame(columns = ['ts', 'rp_path'])
rp_df

for element in rp_dir_list:
    sub_list = os.listdir(rp_data_path + element + '/RP')
    for img in sub_list:
        new_row = {
            'ts' : img[:-4],
            'rp_path' : rp_data_path + element + '/RP/' + img
        }
        rp_df = rp_df.append(new_row, ignore_index=True)
    

rp_df

/tmp/ipykernel_41618/2618502112.py:12: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  rp_df = rp_df.append(new_row, ignore_index=True)
/tmp/ipykernel_41618/2618502112.py:12: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  rp_df = rp_df.append(new_row, ignore_index=True)
/tmp/ipykernel_41618/2618502112.py:12: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  rp_df = rp_df.append(new_row, ignore_index=True)
/tmp/ipykernel_41618/2618502112.py:12: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  rp_df = rp_df.append(new_row, ignore_index=True)
/tmp/ipykernel_41618/2618502112.py:12: FutureWarning: The frame.append method is deprecated and will be remo

/tmp/ipykernel_41618/2618502112.py:12: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  rp_df = rp_df.append(new_row, ignore_index=True)
/tmp/ipykernel_41618/2618502112.py:12: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  rp_df = rp_df.append(new_row, ignore_index=True)
/tmp/ipykernel_41618/2618502112.py:12: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  rp_df = rp_df.append(new_row, ignore_index=True)
/tmp/ipykernel_41618/2618502112.py:12: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  rp_df = rp_df.append(new_row, ignore_index=True)
/tmp/ipykernel_41618/2618502112.py:12: FutureWarning: The frame.append method is deprecated and will be remo

/tmp/ipykernel_41618/2618502112.py:12: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  rp_df = rp_df.append(new_row, ignore_index=True)
/tmp/ipykernel_41618/2618502112.py:12: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  rp_df = rp_df.append(new_row, ignore_index=True)
/tmp/ipykernel_41618/2618502112.py:12: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  rp_df = rp_df.append(new_row, ignore_index=True)
/tmp/ipykernel_41618/2618502112.py:12: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  rp_df = rp_df.append(new_row, ignore_index=True)
/tmp/ipykernel_41618/2618502112.py:12: FutureWarning: The frame.append method is deprecated and will be remo

/tmp/ipykernel_41618/2618502112.py:12: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  rp_df = rp_df.append(new_row, ignore_index=True)
/tmp/ipykernel_41618/2618502112.py:12: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  rp_df = rp_df.append(new_row, ignore_index=True)
/tmp/ipykernel_41618/2618502112.py:12: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  rp_df = rp_df.append(new_row, ignore_index=True)
/tmp/ipykernel_41618/2618502112.py:12: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  rp_df = rp_df.append(new_row, ignore_index=True)
/tmp/ipykernel_41618/2618502112.py:12: FutureWarning: The frame.append method is deprecated and will be remo

/tmp/ipykernel_41618/2618502112.py:12: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  rp_df = rp_df.append(new_row, ignore_index=True)
/tmp/ipykernel_41618/2618502112.py:12: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  rp_df = rp_df.append(new_row, ignore_index=True)
/tmp/ipykernel_41618/2618502112.py:12: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  rp_df = rp_df.append(new_row, ignore_index=True)
/tmp/ipykernel_41618/2618502112.py:12: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  rp_df = rp_df.append(new_row, ignore_index=True)
/tmp/ipykernel_41618/2618502112.py:12: FutureWarning: The frame.append method is deprecated and will be remo

...

/tmp/ipykernel_41618/2618502112.py:12: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  rp_df = rp_df.append(new_row, ignore_index=True)
/tmp/ipykernel_41618/2618502112.py:12: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  rp_df = rp_df.append(new_row, ignore_index=True)
/tmp/ipykernel_41618/2618502112.py:12: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  rp_df = rp_df.append(new_row, ignore_index=True)
/tmp/ipykernel_41618/2618502112.py:12: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  rp_df = rp_df.append(new_row, ignore_index=True)
/tmp/ipykernel_41618/2618502112.py:12: FutureWarning: The frame.append method is deprecated and will be remo

/tmp/ipykernel_41618/2618502112.py:12: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  rp_df = rp_df.append(new_row, ignore_index=True)
/tmp/ipykernel_41618/2618502112.py:12: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  rp_df = rp_df.append(new_row, ignore_index=True)
/tmp/ipykernel_41618/2618502112.py:12: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  rp_df = rp_df.append(new_row, ignore_index=True)
/tmp/ipykernel_41618/2618502112.py:12: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  rp_df = rp_df.append(new_row, ignore_index=True)
/tmp/ipykernel_41618/2618502112.py:12: FutureWarning: The frame.append method is deprecated and will be remo

/tmp/ipykernel_41618/2618502112.py:12: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  rp_df = rp_df.append(new_row, ignore_index=True)
/tmp/ipykernel_41618/2618502112.py:12: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  rp_df = rp_df.append(new_row, ignore_index=True)
/tmp/ipykernel_41618/2618502112.py:12: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  rp_df = rp_df.append(new_row, ignore_index=True)
/tmp/ipykernel_41618/2618502112.py:12: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  rp_df = rp_df.append(new_row, ignore_index=True)
/tmp/ipykernel_41618/2618502112.py:12: FutureWarning: The frame.append method is deprecated and will be remo

/tmp/ipykernel_41618/2618502112.py:12: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  rp_df = rp_df.append(new_row, ignore_index=True)
/tmp/ipykernel_41618/2618502112.py:12: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  rp_df = rp_df.append(new_row, ignore_index=True)
/tmp/ipykernel_41618/2618502112.py:12: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  rp_df = rp_df.append(new_row, ignore_index=True)
/tmp/ipykernel_41618/2618502112.py:12: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  rp_df = rp_df.append(new_row, ignore_index=True)
/tmp/ipykernel_41618/2618502112.py:12: FutureWarning: The frame.append method is deprecated and will be remo

ts                                       rp_path
0      1601192520  ./RPdata/user04/1601163000/RP/1601192520.png
1      1601182080  ./RPdata/user04/1601163000/RP/1601182080.png
2      1601191020  ./RPdata/user04/1601163000/RP/1601191020.png
3      1601200500  ./RPdata/user04/1601163000/RP/1601200500.png
4      1601192640  ./RPdata/user04/1601163000/RP/1601192640.png
...           ...                                           ...
19719  1599447960  ./RPdata/user04/1599430860/RP/1599447960.png
19720  1599433260  ./RPdata/user04/1599430860/RP/1599433260.png
19721  1599436680  ./RPdata/user04/1599430860/RP/1599436680.png
19722  1599449580  ./RPdata/user04/1599430860/RP/1599449580.png
19723  1599464700  ./RPdata/user04/1599430860/RP/1599464700.png

[19724 rows x 2 columns]

In [15]:
df = pd.merge(df, rp_df, on = 'ts')

In [16]:
df

ts       action  actionOption  activity  \
0      1598829240         meal           121         4   
1      1598829300         meal           121         3   
2      1598829360         meal           121         4   
3      1598829420         meal           121         3   
4      1598829480         meal           121         3   
...           ...          ...           ...       ...   
20390  1601208840  outdoor_act           751         4   
20391  1601208900  outdoor_act           751         3   
20392  1601208960  outdoor_act           751         3   
20393  1601209020  outdoor_act           751         3   
20394  1601209080  outdoor_act           751         3   

                                            rp_path  
0      ./RPdata/user04/1598828400/RP/1598829240.png  
1      ./RPdata/user04/1598828400/RP/1598829300.png  
2      ./RPdata/user04/1598828400/RP/1598829360.png  
3      ./RPdata/user04/1598828400/RP/1598829420.png  
4      ./RPdata/user04/1598828400/RP/1598829480.png  
...                                             ...  
20390  ./RPdata/user04/1601163000/RP/1601208840.png  
20391  ./RPdata/user04/1601163000/RP/1601208900.png  
20392  ./RPdata/user04/1601163000/RP/1601208960.png  
20393  ./RPdata/user04/1601163000/RP/1601209020.png  
20394  ./RPdata/user04/1601163000/RP/1601209080.png  

[20395 rows x 5 columns]

In [17]:
from sklearn.preprocessing import LabelEncoder

In [18]:
le = LabelEncoder()

df['actionOption'] =le.fit_transform(df['actionOption'])

In [19]:
df

ts       action  actionOption  activity  \
0      1598829240         meal             9         4   
1      1598829300         meal             9         3   
2      1598829360         meal             9         4   
3      1598829420         meal             9         3   
4      1598829480         meal             9         3   
...           ...          ...           ...       ...   
20390  1601208840  outdoor_act            21         4   
20391  1601208900  outdoor_act            21         3   
20392  1601208960  outdoor_act            21         3   
20393  1601209020  outdoor_act            21         3   
20394  1601209080  outdoor_act            21         3   

                                            rp_path  
0      ./RPdata/user04/1598828400/RP/1598829240.png  
1      ./RPdata/user04/1598828400/RP/1598829300.png  
2      ./RPdata/user04/1598828400/RP/1598829360.png  
3      ./RPdata/user04/1598828400/RP/1598829420.png  
4      ./RPdata/user04/1598828400/RP/1598829480.png  
...                                             ...  
20390  ./RPdata/user04/1601163000/RP/1601208840.png  
20391  ./RPdata/user04/1601163000/RP/1601208900.png  
20392  ./RPdata/user04/1601163000/RP/1601208960.png  
20393  ./RPdata/user04/1601163000/RP/1601209020.png  
20394  ./RPdata/user04/1601163000/RP/1601209080.png  

[20395 rows x 5 columns]

Train process

In [20]:
device = torch.device('cuda') if torch.cuda.is_available() else torch.device('cpu')

In [21]:
CFG = {
    'IMG_SIZE':224,
    'EPOCHS':30,
    'LEARNING_RATE':3e-4,
    'BATCH_SIZE':16,
    'SEED':42
}

In [22]:
def seed_everything(seed):
    random.seed(seed)
    os.environ['PYTHONHASHSEED'] = str(seed)
    np.random.seed(seed)
    torch.manual_seed(seed)
    torch.cuda.manual_seed(seed)
    torch.backends.cudnn.deterministic = True
    torch.backends.cudnn.benchmark = True

seed_everything(CFG['SEED'])

In [23]:
train, val, _, _ = train_test_split(df, df['actionOption'], test_size=0.2, random_state=CFG['SEED'])

In [24]:
train

ts         action  actionOption  activity  \
7901   1599818520           meal             9         4   
7431   1599777840  personal_care            12         3   
20110  1601192040           work            14         3   
3014   1599188700           work            13         0   
19617  1601121240      household             2         4   
...           ...            ...           ...       ...   
11284  1600169700    outdoor_act            22         2   
11964  1600248240           work            13         3   
5390   1599443760           work            13         3   
860    1598921520           work            13         3   
15795  1600690020    outdoor_act            23         3   

                                            rp_path  
7901   ./RPdata/user04/1599776160/RP/1599818520.png  
7431   ./RPdata/user04/1599776160/RP/1599777840.png  
20110  ./RPdata/user04/1601163000/RP/1601192040.png  
3014   ./RPdata/user04/1599174600/RP/1599188700.png  
19617  ./RPdata/user04/1601079300/RP/1601121240.png  
...                                             ...  
11284  ./RPdata/user04/1600122300/RP/1600169700.png  
11964  ./RPdata/user04/1600207800/RP/1600248240.png  
5390   ./RPdata/user04/1599430860/RP/1599443760.png  
860    ./RPdata/user04/1598912400/RP/1598921520.png  
15795  ./RPdata/user04/1600640400/RP/1600690020.png  

[16316 rows x 5 columns]

In [25]:
val

ts       action  actionOption  activity  \
19772  1601171760       travel             4         0   
351    1598852400         work            13         3   
5333   1599440340         work            13         3   
12011  1600251060  outdoor_act            23         4   
11717  1600233420         work            13         3   
...           ...          ...           ...       ...   
2950   1599183120         work            13         3   
18597  1601017080         work            13         3   
1393   1598960580  outdoor_act            21         2   
17907  1600938180         work            13         3   
17273  1600867260  socialising            17         3   

                                            rp_path  
19772  ./RPdata/user04/1601163000/RP/1601171760.png  
351    ./RPdata/user04/1598828400/RP/1598852400.png  
5333   ./RPdata/user04/1599430860/RP/1599440340.png  
12011  ./RPdata/user04/1600207800/RP/1600251060.png  
11717  ./RPdata/user04/1600207800/RP/1600233420.png  
...                                             ...  
2950   ./RPdata/user04/1599174600/RP/1599183120.png  
18597  ./RPdata/user04/1600986000/RP/1601017080.png  
1393   ./RPdata/user04/1598912400/RP/1598960580.png  
17907  ./RPdata/user04/1600899900/RP/1600938180.png  
17273  ./RPdata/user04/1600816860/RP/1600867260.png  

[4079 rows x 5 columns]

In [26]:
tfms = A.Compose([
    A.Resize(width=CFG['IMG_SIZE'], height=CFG['IMG_SIZE']),
    A.Normalize()
], p=1)

In [27]:
class CustomDataset(Dataset):
    def __init__(self, df, rp_path_list, label_list, tfms=None):
        super().__init__()
        self.df = df
        self.rp_path_list = rp_path_list
        self.label_list = label_list
        self.tfms=tfms
    
    def __len__(self):
        return len(self.rp_path_list)
    
    def __getitem__(self, idx):
        img = cv2.imread(self.rp_path_list[idx])
        img = cv2.cvtColor(img, cv2.COLOR_BGR2RGB)
        image = self.tfms(image=img)['image']
        image = torch.tensor(np.array(image)).permute(2, 0, 1)
        
        if self.label_list is not None:
            label = self.label_list[idx]
            return image, label
        else:
            return image

In [28]:
train_dataset = CustomDataset(df=df, rp_path_list=train['rp_path'].values, label_list=train['actionOption'].values, tfms=tfms)
train_loader = DataLoader(train_dataset, batch_size = CFG['BATCH_SIZE'], shuffle=True, num_workers=0)

val_dataset = CustomDataset(df=df,rp_path_list=val['rp_path'].values, label_list=val['actionOption'].values, tfms=tfms)
val_loader = DataLoader(val_dataset, batch_size = CFG['BATCH_SIZE'], shuffle=False, num_workers=0)

In [29]:
def train(model, optimizer, train_loader, val_loader, scheduler, device):
    model.to(device)
    criterion = nn.CrossEntropyLoss().to(device)
    
    best_val_score = 0
    best_model = None
    
    for epoch in range(1, CFG['EPOCHS']+1):
        model.train()
        train_loss = []
        for images, labels in tqdm(iter(train_loader)):
            images = images.to(device)
            labels = labels.to(device)
            
            optimizer.zero_grad()
            
            output = model(images)
            loss = criterion(output, labels)
            
            loss.backward()
            optimizer.step()
            
            train_loss.append(loss.item())
                    
        _val_loss, _val_score = validation(model, criterion, val_loader, device)
        _train_loss = np.mean(train_loss)
        print(f'Epoch [{epoch}], Train Loss : [{_train_loss:.5f}] Val Loss : [{_val_loss:.5f}] Val F1 : [{_val_score:.5f}]')
        
        if scheduler is not None:
            scheduler.step(_val_score)
            
        if best_val_score < _val_score:
            best_val_score = _val_score
            best_model = model
    
    return best_model

In [30]:
def validation(model, criterion, val_loader, device):
    model.eval()
    val_loss = []
    preds, trues = [], []
    
    with torch.no_grad():
        for images, labels in tqdm(iter(val_loader)):
            images = images.to(device)
            labels = labels.to(device)
            
            logit = model(images)
            
            loss = criterion(logit, labels)
            
            val_loss.append(loss.item())
            
            preds += logit.argmax(1).detach().cpu().numpy().tolist()
            trues += labels.detach().cpu().numpy().tolist()
        
        _val_loss = np.mean(val_loss)
    
    _val_score = f1_score(trues, preds, average='macro')
    return _val_loss, _val_score

In [31]:
model = ResNet18(64, 26)
model.eval()
optimizer = torch.optim.Adam(params = model.parameters(), lr = CFG["LEARNING_RATE"])
scheduler = torch.optim.lr_scheduler.ReduceLROnPlateau(optimizer, mode='max', factor=0.5, patience=2,threshold_mode='abs',min_lr=1e-8, verbose=True)

infer_model = train(model, optimizer, train_loader, val_loader, scheduler, device)

  0%|          | 0/1020 [00:00<?, ?it/s]

  0%|          | 0/255 [00:00<?, ?it/s]

Epoch [1], Train Loss : [2.22214] Val Loss : [2.16089] Val F1 : [0.07519]


  0%|          | 0/1020 [00:00<?, ?it/s]

  0%|          | 0/255 [00:00<?, ?it/s]

...

  0%|          | 0/255 [00:00<?, ?it/s]

Epoch [29], Train Loss : [1.52126] Val Loss : [1.82851] Val F1 : [0.22291]


  0%|          | 0/1020 [00:00<?, ?it/s]

  0%|          | 0/255 [00:00<?, ?it/s]

Epoch [30], Train Loss : [1.52098] Val Loss : [1.84187] Val F1 : [0.22522]
